In [1]:
import pandas as pd
import numpy as np

In [2]:
!pip install folium


Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [3]:
!pip install geopy

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [4]:
from geopy.distance import geodesic

In [5]:
#hurricane_data = pd.read_csv('/content/ibtracs.EP.list.csv', nrows=500)
hurricane_data = pd.read_csv('/content/ibtracs.NA.csv')

hurricane_df = pd.DataFrame(hurricane_data, columns=['SID', 'SEASON', 'BASIN', 'LAT', 'LON', 'USA_ROCI', 'USA_RMW', 'ISO_TIME', 'BOM_EYE'])
hurricane_df.drop(hurricane_df.index[0], inplace=True)
hurricane_df["ISO_TIME"] = pd.to_datetime(hurricane_df["ISO_TIME"], errors='coerce')
hurricane_df["MONTH"] = hurricane_df["ISO_TIME"].dt.month
hurricane_df['USA_RMW'] = pd.to_numeric(hurricane_df['USA_RMW'], errors='coerce')
hurricane_df['USA_ROCI'] = pd.to_numeric(hurricane_df['USA_ROCI'], errors='coerce')
hurricane_df['RADIUS_KM'] = hurricane_df['USA_RMW'].apply(lambda x: float(x) * 1.852)
hurricane_df['LON'] = pd.to_numeric(hurricane_df['LON'], errors='coerce')
hurricane_df['LAT'] = pd.to_numeric(hurricane_df['LAT'], errors='coerce')
hurricane_df.dropna(subset=['LAT', 'LON'], inplace=True)
hurricane_df


/usr/local/lib/python3.8/dist-packages/IPython/core/interactiveshell.py:3326: DtypeWarning: Columns (1,2,3,8,9,14,19,20,23,24,161,162) have mixed types.Specify dtype option on import or set low_memory=False.
  exec(code_obj, self.user_global_ns, self.user_ns)


SID SEASON BASIN      LAT      LON  USA_ROCI  USA_RMW  \
1       1851175N26270   1851   NaN  26.1000 -90.4000       NaN      NaN   
2       1851175N26270   1851   NaN  26.2001 -90.6999       NaN      NaN   
3       1851175N26270   1851   NaN  26.3000 -91.0000       NaN      NaN   
4       1851175N26270   1851   NaN  26.3999 -91.3001       NaN      NaN   
5       1851175N26270   1851   NaN  26.5000 -91.6000       NaN      NaN   
...               ...    ...   ...      ...      ...       ...      ...   
125640  2022309N16290   2022   NaN  31.3000 -84.5000     220.0     90.0   
125641  2022309N16290   2022   NaN  32.1296 -84.6324     285.0    170.0   
125642  2022309N16290   2022   NaN  33.2000 -84.5000     350.0    250.0   
125643  2022309N16290   2022   NaN  34.5286 -84.0494     420.0    325.0   
125644  2022309N16290   2022   NaN  36.0000 -83.4000     490.0    400.0   

                  ISO_TIME BOM_EYE  MONTH  RADIUS_KM  
1      1851-06-23 12:00:00              6        NaN  
2      1851-06-23 15:00:00              6        NaN  
3      1851-06-23 18:00:00              6        NaN  
4      1851-06-23 21:00:00              6        NaN  
5      1851-06-24 00:00:00              6        NaN  
...                    ...     ...    ...        ...  
125640 2022-11-11 06:00:00             11     166.68  
125641 2022-11-11 09:00:00             11     314.84  
125642 2022-11-11 12:00:00             11     463.00  
125643 2022-11-11 15:00:00             11     601.90  
125644 2022-11-11 18:00:00             11     740.80  

[125644 rows x 11 columns]

In [7]:
# Get only 1 month data 09/2022 for testing
filtered_hurricane_df = hurricane_df[(hurricane_df["SEASON"] == 2022) & (hurricane_df["MONTH"] == 9)]
filtered_hurricane_df = filtered_hurricane_df.reset_index(drop=True)
filtered_hurricane_df


SID SEASON BASIN      LAT      LON  USA_ROCI  USA_RMW  \
0    2022239N12324   2022   NaN  15.7000 -51.3000     150.0     90.0   
1    2022239N12324   2022   NaN  15.7999 -51.6625     150.0     90.0   
2    2022239N12324   2022   NaN  15.9000 -52.1000     150.0     90.0   
3    2022239N12324   2022   NaN  15.9849 -52.5702     150.0     90.0   
4    2022239N12324   2022   NaN  16.1000 -53.1000     150.0     90.0   
..             ...    ...   ...      ...      ...       ...      ...   
502  2022265N15348   2022   NaN  21.4000 -20.6000     180.0     40.0   
503  2022265N15348   2022   NaN  21.9725 -20.5116     180.0     40.0   
504  2022265N15348   2022   NaN  22.5000 -20.4333     180.0     40.0   
505  2022265N15348   2022   NaN  22.9300 -20.3642     180.0     40.0   
506  2022265N15348   2022   NaN  23.3000 -20.3000     180.0     40.0   

               ISO_TIME BOM_EYE  MONTH  RADIUS_KM  
0   2022-09-01 00:00:00              9     166.68  
1   2022-09-01 03:00:00              9     166.68  
2   2022-09-01 06:00:00              9     166.68  
3   2022-09-01 09:00:00              9     166.68  
4   2022-09-01 12:00:00              9     166.68  
..                  ...     ...    ...        ...  
502 2022-09-24 18:00:00              9      74.08  
503 2022-09-24 21:00:00              9      74.08  
504 2022-09-25 00:00:00              9      74.08  
505 2022-09-25 03:00:00              9      74.08  
506 2022-09-25 06:00:00              9      74.08  

[507 rows x 11 columns]

In [8]:
# Draw hurricanes on the map
import folium

mean_lat = filtered_hurricane_df['LAT'].mean()
mean_lon = filtered_hurricane_df['LON'].mean()
map_hurricanes = folium.Map(location=[mean_lat, mean_lon], zoom_start=5, min_zoom=4, max_zoom=7)

# #FFA500
# mediumpurple
for i, row in filtered_hurricane_df.iterrows():
    lat = row['LAT']
    lon = row['LON']
    folium.CircleMarker(location=[lat, lon], 
                        radius_fixed= True,
                        radius = row['RADIUS_KM'], 
                        fill=True, color='mediumpurple', opacity = 0.3, fill_color = 'mediumpurple', fill_opacity=0.3, 
                        popup = row['ISO_TIME'],
                        tooltip='LAT: {} \LON: {} \RADIUS_KM: {}'.format(row['LAT'],row['LON'],row['RADIUS_KM'])).add_to(map_hurricanes)

map_hurricanes

In [9]:
# Get the loan data
# This is not the full dataset

loan_data = pd.read_csv('/content/loans.csv', encoding= 'unicode_escape')
#loan_data = pd.read_csv('/content/loans.csv', nrows = 1000)

loan_df = pd.DataFrame(loan_data, columns=['Loan Name', 'Property Type', 'State','City', 'Zip Code', 'Reporting Date'])
states = ['NC', 'SC', 'GA', 'LA', 'FL']
loan_df = loan_df[loan_df['State'].isin(states)]
loan_df['City_State'] = loan_df.apply(lambda x: x['City'] + ', ' + x['State'], axis=1)
loan_df


Loan Name Property Type State            City  \
1                       Yacht Club   Multifamily    FL       Bradenton   
3      Breckinridge Vue Apartments   Multifamily    GA          Duluth   
4      Verde At Mccullough Station   Multifamily    NC       Charlotte   
6        Waterstone At Carrollwood   Multifamily    FL           Tampa   
8         The Point At Bella Grove   Multifamily    FL        Sarasota   
...                            ...           ...   ...             ...   
4991                  Valley Brook           MHC    GA  Stone Mountain   
4993            Pine Village North   Multifamily    GA          Smyrna   
4995               Colony Club MHP           MHC    FL    Winter Haven   
4997            Tranquil Acres MHP           MHC    FL      Auburndale   
4999  Falcon Trace Apartment Homes   Multifamily    FL         Orlando   

     Zip Code Reporting Date          City_State  
1       34212     2022-12-02       Bradenton, FL  
3       30096     2022-12-02          Duluth, GA  
4       28262     2022-12-02       Charlotte, NC  
6       33618     2022-12-02           Tampa, FL  
8       34243     2022-12-02        Sarasota, FL  
...       ...            ...                 ...  
4991    30087     2023-01-25  Stone Mountain, GA  
4993    30080     2023-01-25          Smyrna, GA  
4995    33881     2023-01-25    Winter Haven, FL  
4997    33823     2023-01-25      Auburndale, FL  
4999    32837     2023-01-25         Orlando, FL  

[1867 rows x 7 columns]

In [10]:
# Import the city data to get lat and lon for properties
# This data can be changed later

city_data = pd.read_csv('/content/uscities.csv')
city_df = pd.DataFrame(city_data, columns=['city', 'state_id', 'lat', 'lng'])
city_df

city state_id      lat       lng
0          New York       NY  40.6943  -73.9249
1       Los Angeles       CA  34.1141 -118.4068
2           Chicago       IL  41.8375  -87.6866
3             Miami       FL  25.7840  -80.2101
4            Dallas       TX  32.7935  -96.7667
...             ...      ...      ...       ...
30404      Drummond       ID  43.9996 -111.3433
30405  Lost Springs       WY  42.7652 -104.9255
30406         Provo       SD  43.1937 -103.8329
30407     Goldcreek       MT  46.5838 -112.9284
30408        Le Roy       IA  40.8779  -93.5926

[30409 rows x 4 columns]

In [11]:
loan_with_coords_df = pd.merge(loan_df, city_df, left_on=['City', 'State'], right_on=['city', 'state_id'], how='left')
loan_with_coords_df = loan_with_coords_df.dropna(subset=['lat', 'lng'], how='any')
loan_with_coords_df['lng'] = pd.to_numeric(loan_with_coords_df['lng'], errors='coerce')
loan_with_coords_df['lat'] = pd.to_numeric(loan_with_coords_df['lat'], errors='coerce')
loan_with_coords_df = loan_with_coords_df.rename(columns={'lat': 'LAT', 'lng': 'LON'})
loan_with_coords_df = loan_with_coords_df.reset_index(drop=True)
loan_with_coords_df


Loan Name Property Type State            City  \
0                       Yacht Club   Multifamily    FL       Bradenton   
1      Breckinridge Vue Apartments   Multifamily    GA          Duluth   
2      Verde At Mccullough Station   Multifamily    NC       Charlotte   
3        Waterstone At Carrollwood   Multifamily    FL           Tampa   
4         The Point At Bella Grove   Multifamily    FL        Sarasota   
...                            ...           ...   ...             ...   
1739                  Valley Brook           MHC    GA  Stone Mountain   
1740            Pine Village North   Multifamily    GA          Smyrna   
1741               Colony Club MHP           MHC    FL    Winter Haven   
1742            Tranquil Acres MHP           MHC    FL      Auburndale   
1743  Falcon Trace Apartment Homes   Multifamily    FL         Orlando   

     Zip Code Reporting Date          City_State            city state_id  \
0       34212     2022-12-02       Bradenton, FL       Bradenton       FL   
1       30096     2022-12-02          Duluth, GA          Duluth       GA   
2       28262     2022-12-02       Charlotte, NC       Charlotte       NC   
3       33618     2022-12-02           Tampa, FL           Tampa       FL   
4       34243     2022-12-02        Sarasota, FL        Sarasota       FL   
...       ...            ...                 ...             ...      ...   
1739    30087     2023-01-25  Stone Mountain, GA  Stone Mountain       GA   
1740    30080     2023-01-25          Smyrna, GA          Smyrna       GA   
1741    33881     2023-01-25    Winter Haven, FL    Winter Haven       FL   
1742    33823     2023-01-25      Auburndale, FL      Auburndale       FL   
1743    32837     2023-01-25         Orlando, FL         Orlando       FL   

          LAT      LON  
0     27.4901 -82.5757  
1     34.0053 -84.1492  
2     35.2083 -80.8303  
3     27.9945 -82.4447  
4     27.3387 -82.5432  
...       ...      ...  
1739  33.8035 -84.1723  
1740  33.8633 -84.5168  
1741  28.0118 -81.7014  
1742  28.0963 -81.8012  
1743  28.4773 -81.3370  

[1744 rows x 11 columns]

In [ ]:
# Show all properties on the map
# for i, row in loan_with_coords_df.iterrows():
#     folium.CircleMarker(location=(row['LAT'], row['LON']),
#                        radius=3,
#                        color='red',
#                        fill=True,
#                        fill_color='red',
#                        tooltip=row['Loan Name']).add_to(map_hurricanes)
# map_hurricanes

In [ ]:
# # Only show exposed or not
# # Version 1
# def is_exposed(property_lat, property_long, hurricane_lat, hurricane_long, radius_km):
#     #print("property lat: ", property_lat, " long: ", property_long)
#     #print("hurricane lat: ", hurricane_lat, " long: ", hurricane_long, " radius_km: ", radius_km)
#     property_point = (property_lat, property_long)
#     hurricane_point = (hurricane_lat, hurricane_long)
#     distance = geodesic(property_point, hurricane_point).km
#     #print("distance: ", distance)
#     if distance <= radius_km:
#         return True
#     else:
#         return False

In [12]:
# Show Moderate Risk Properties
# Version 2
def is_exposed_2(property_lat, property_long, hurricane_lat, hurricane_long, radius_km):
    #print("property lat: ", property_lat, " long: ", property_long)
    #print("hurricane lat: ", hurricane_lat, " long: ", hurricane_long, " radius_km: ", radius_km)
    property_point = (property_lat, property_long)
    hurricane_point = (hurricane_lat, hurricane_long)
    distance = geodesic(property_point, hurricane_point).km
    #print("distance: ", distance)
    if distance <= radius_km:
        return "Exposed"
    elif distance - radius_km < 20:
        return "Risk"
    else:
        return "Safe"

In [ ]:
# Version 1
# loan_with_coords_df['exposed'] = np.nan

# for i in range(loan_with_coords_df.shape[0]):
#     for j in range(filtered_hurricane_df.shape[0]):
#         if is_exposed(loan_with_coords_df.loc[i, 'LAT'], loan_with_coords_df.loc[i, 'LON'], 
#                       filtered_hurricane_df.loc[j, 'LAT'], filtered_hurricane_df.loc[j, 'LON'], 
#                       filtered_hurricane_df.loc[j, 'RADIUS_KM']):
#             loan_with_coords_df.loc[i, 'exposed'] = True
#             break
#     if pd.isna(loan_with_coords_df.loc[i, 'exposed']):
#         loan_with_coords_df.loc[i, 'exposed'] = False
# loan_with_coords_df


Loan Name Property Type State            City  \
0                       Yacht Club   Multifamily    FL       Bradenton   
1      Breckinridge Vue Apartments   Multifamily    GA          Duluth   
2      Verde At Mccullough Station   Multifamily    NC       Charlotte   
3        Waterstone At Carrollwood   Multifamily    FL           Tampa   
4         The Point At Bella Grove   Multifamily    FL        Sarasota   
...                            ...           ...   ...             ...   
1739                  Valley Brook           MHC    GA  Stone Mountain   
1740            Pine Village North   Multifamily    GA          Smyrna   
1741               Colony Club MHP           MHC    FL    Winter Haven   
1742            Tranquil Acres MHP           MHC    FL      Auburndale   
1743  Falcon Trace Apartment Homes   Multifamily    FL         Orlando   

     Zip Code Reporting Date          City_State            city state_id  \
0       34212     2022-12-02       Bradenton, FL       Bradenton       FL   
1       30096     2022-12-02          Duluth, GA          Duluth       GA   
2       28262     2022-12-02       Charlotte, NC       Charlotte       NC   
3       33618     2022-12-02           Tampa, FL           Tampa       FL   
4       34243     2022-12-02        Sarasota, FL        Sarasota       FL   
...       ...            ...                 ...             ...      ...   
1739    30087     2023-01-25  Stone Mountain, GA  Stone Mountain       GA   
1740    30080     2023-01-25          Smyrna, GA          Smyrna       GA   
1741    33881     2023-01-25    Winter Haven, FL    Winter Haven       FL   
1742    33823     2023-01-25      Auburndale, FL      Auburndale       FL   
1743    32837     2023-01-25         Orlando, FL         Orlando       FL   

          LAT      LON exposed  
0     27.4901 -82.5757   False  
1     34.0053 -84.1492   False  
2     35.2083 -80.8303   False  
3     27.9945 -82.4447   False  
4     27.3387 -82.5432   False  
...       ...      ...     ...  
1739  33.8035 -84.1723   False  
1740  33.8633 -84.5168   False  
1741  28.0118 -81.7014   False  
1742  28.0963 -81.8012   False  
1743  28.4773 -81.3370    True  

[1744 rows x 12 columns]

In [ ]:
# Version 1
# Draw all properties on the map
# Exposed properties -> red dot
# Not exposed properties -> green dot

# for i, row in loan_with_coords_df.iterrows():
#     if row['exposed'] == True:
#         color = 'red'
#     else:
#         color = 'green'
#     folium.CircleMarker(location=(row['LAT'], row['LON']),
#                        radius=3,
#                        color=color,
#                        fill=True,
#                        fill_color=color,
#                        tooltip=row['Loan Name']).add_to(map_hurricanes)
# map_hurricanes

In [13]:
# Version 2 
# 1 month hurricane data -> Took 5 minutes to run
loan_with_coords_df['expose_status'] = np.nan

for i in range(loan_with_coords_df.shape[0]):
    current_status = loan_with_coords_df.loc[i, 'expose_status']
    for j in range(filtered_hurricane_df.shape[0]):
        if current_status == "Exposed":
          break
        new_status = is_exposed_2(loan_with_coords_df.loc[i, 'LAT'], loan_with_coords_df.loc[i, 'LON'], 
                      filtered_hurricane_df.loc[j, 'LAT'], filtered_hurricane_df.loc[j, 'LON'], 
                      filtered_hurricane_df.loc[j, 'RADIUS_KM'])
        if pd.isna(current_status) or (current_status == "Safe" and (new_status == "Risk" or new_status == 'Exposed')) or (current_status == "Risk" and new_status == "Exposed"):
            loan_with_coords_df.loc[i, 'expose_status'] = new_status
            current_status = new_status

loan_with_coords_df

Loan Name Property Type State            City  \
0                       Yacht Club   Multifamily    FL       Bradenton   
1      Breckinridge Vue Apartments   Multifamily    GA          Duluth   
2      Verde At Mccullough Station   Multifamily    NC       Charlotte   
3        Waterstone At Carrollwood   Multifamily    FL           Tampa   
4         The Point At Bella Grove   Multifamily    FL        Sarasota   
...                            ...           ...   ...             ...   
1739                  Valley Brook           MHC    GA  Stone Mountain   
1740            Pine Village North   Multifamily    GA          Smyrna   
1741               Colony Club MHP           MHC    FL    Winter Haven   
1742            Tranquil Acres MHP           MHC    FL      Auburndale   
1743  Falcon Trace Apartment Homes   Multifamily    FL         Orlando   

     Zip Code Reporting Date          City_State            city state_id  \
0       34212     2022-12-02       Bradenton, FL       Bradenton       FL   
1       30096     2022-12-02          Duluth, GA          Duluth       GA   
2       28262     2022-12-02       Charlotte, NC       Charlotte       NC   
3       33618     2022-12-02           Tampa, FL           Tampa       FL   
4       34243     2022-12-02        Sarasota, FL        Sarasota       FL   
...       ...            ...                 ...             ...      ...   
1739    30087     2023-01-25  Stone Mountain, GA  Stone Mountain       GA   
1740    30080     2023-01-25          Smyrna, GA          Smyrna       GA   
1741    33881     2023-01-25    Winter Haven, FL    Winter Haven       FL   
1742    33823     2023-01-25      Auburndale, FL      Auburndale       FL   
1743    32837     2023-01-25         Orlando, FL         Orlando       FL   

          LAT      LON expose_status  
0     27.4901 -82.5757          Safe  
1     34.0053 -84.1492          Safe  
2     35.2083 -80.8303          Safe  
3     27.9945 -82.4447          Safe  
4     27.3387 -82.5432          Safe  
...       ...      ...           ...  
1739  33.8035 -84.1723          Safe  
1740  33.8633 -84.5168          Safe  
1741  28.0118 -81.7014          Safe  
1742  28.0963 -81.8012          Safe  
1743  28.4773 -81.3370       Exposed  

[1744 rows x 12 columns]

In [14]:
# Version 2
# Draw all properties on the map
# Exposed properties -> red dot
# Not exposed properties -> green dot

for i, row in loan_with_coords_df.iterrows():
    if row['expose_status'] == 'Exposed':
        color = 'red'
    elif row['expose_status'] == 'Risk':
        color = '#FFA500'
    else:
        color = 'green'
    folium.CircleMarker(location=(row['LAT'], row['LON']),
                       radius=3,
                       color=color,
                       fill=True,
                       fill_color=color,
                       tooltip=row['Loan Name']).add_to(map_hurricanes)
map_hurricanes